In [1]:
# reload modules
%load_ext autoreload
%autoreload 2

In [9]:
import sys
import os
sys.path.append('./src')
os.environ['NDF_SOURCE_DIR'] = './src/ndf_robot'

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="1"

In [10]:
# !../ndf_robot/scripts/download_demo_weights.sh
# !../ndf_robot/scripts/download_demo_data.sh

In [11]:
import os.path as osp
import torch
import numpy as np
import trimesh
import random
import copy
from scipy.spatial.transform import Rotation
from imageio import get_writer, imread

from ndf_robot.utils import path_util
import ndf_robot.model.vnn_occupancy_net_pointnet_dgcnn as vnn_occupancy_network
from ndf_robot.eval.ndf_alignment import NDFAlignmentCheck

###  Dataloader for teddies

In [19]:
from ndf_robot.training.acid_dataset import AcidDataset
from ndf_robot.utils.plotly_save import plot_point_clouds

root_dir = "/home/sjindal/work/ACID/data_ndf"
category = ["teddy"]

train_dataset = AcidDataset(root_dir, "train", category, transform=True, all_points=True)
val_dataset = AcidDataset(root_dir, "val", category, transform=False, all_points=True)
print(len(train_dataset), len(val_dataset))
data, occ = val_dataset[100]

plot_point_clouds(data["point_cloud"], "red")

2198 943


### NDF Alignment Check - Anthony et. al. version

In [5]:
seed = 0
np.random.seed(seed)
random.seed(seed)
torch.random.manual_seed(seed)

# see the demo object descriptions folder for other object models you can try
obj_model1 = osp.join(path_util.get_ndf_demo_obj_descriptions(), 'mug_centered_obj_normalized/28f1e7bc572a633cb9946438ed40eeb9/models/model_normalized.obj')
obj_model2 = osp.join(path_util.get_ndf_demo_obj_descriptions(), 'mug_centered_obj_normalized/586e67c53f181dc22adf8abaa25e0215/models/model_normalized.obj')

# colab has a weird thing showing the .obj versions of one of these models, so we quickly convert them to .stl files
mesh1 = trimesh.load(obj_model1, process=False); mesh1_stl = 'stl_model1.stl'; mesh1.export(mesh1_stl)
mesh2 = trimesh.load(obj_model2, process=False); mesh2_stl = 'stl_model2.stl'; mesh2.export(mesh2_stl)
model_path = osp.join(path_util.get_ndf_model_weights(), 'ndf_demo_mug_weights.pth')  


scale1 = 0.3
scale2 = 0.3
mesh1 = trimesh.load(mesh1_stl, process=False)
mesh1.apply_scale(scale1)
mesh2 = trimesh.load(mesh2_stl, process=False) # different instance, different scaling
mesh2.apply_scale(scale2)
# mesh2 = trimesh.load(mesh1_stl, process=False)  # use same object model to debug SE(3) equivariance
# mesh2.apply_scale(scale1)

# apply a random initial rotation to the new shape
quat = np.random.random(4)
quat = quat / np.linalg.norm(quat)
rot = np.eye(4)
rot[:-1, :-1] = Rotation.from_quat(quat).as_matrix()
mesh2.apply_transform(rot)

pcd1 = mesh1.sample(5000)
pcd2 = mesh2.sample(5000)  # point cloud representing different shape
# pcd2 = copy.deepcopy(pcd1)  # debug with the exact same point cloud
# pcd2 = mesh1.sample(5000)  # debug with same shape but different sampled points

show_mesh1 = mesh1.copy()
show_mesh2 = mesh2.copy()

offset = 0.2
show_mesh1.apply_translation([-1.0 * offset, 0, 0])
show_mesh2.apply_translation([offset, 0, 0])

scene = trimesh.Scene()
scene.add_geometry([show_mesh1, show_mesh2])
# print('Showing demo shapes')
# scene.show()

['stl_model1.stl', 'stl_model2.stl']

In [6]:
class AttrDict(dict):
  __getattr__ = dict.__getitem__
  __setattr__ = dict.__setitem__

args = {
    'seed': 0,
    'show_recon': False,
    'sigma': 0.025,
    'visualize':True,
    'video': False
}
args = AttrDict(args)

model = vnn_occupancy_network.VNNOccNet(latent_dim=256, model_type='pointnet', return_features=True, sigmoid=True).cuda()
model.load_state_dict(torch.load(model_path))

# take a look at the optimization process that runs in the sample_pts method to find frame correspondence here: 
# https://github.com/anthonysimeonov/ndf_robot/blob/master/src/ndf_robot/eval/ndf_alignment.py#L115
ndf_alignment = NDFAlignmentCheck(model, pcd1, pcd2, sigma=args.sigma, trimesh_viz=args.visualize)
T1, T2 = ndf_alignment.sample_pts(show_recon=True, return_scene=True, render_video=args.video)

i: 0, losses: 0.010795, 0.010584, 0.009302, 0.010633, 0.009545, 0.009651, 0.009878, 0.010203, 0.011904, 0.009214
vid plot idx:  6
i: 100, losses: 0.005278, 0.003369, 0.004442, 0.006251, 0.003655, 0.005375, 0.005270, 0.005794, 0.004887, 0.002819
i: 200, losses: 0.004564, 0.002801, 0.002888, 0.006154, 0.002804, 0.003398, 0.004598, 0.005630, 0.003417, 0.002803
i: 300, losses: 0.004560, 0.002797, 0.002809, 0.006151, 0.002797, 0.003372, 0.003374, 0.005268, 0.003385, 0.002797
i: 400, losses: 0.003673, 0.002805, 0.002805, 0.006151, 0.002800, 0.003374, 0.003372, 0.005249, 0.003375, 0.002805
best loss: 0.002804, best_idx: 4


In [23]:
fig, scene  = ndf_alignment.visualize_alignment(pcd1, pcd2, T1, T2, transform = rot, show_plotly=True, show_trimesh=True)
fig.update_traces(showlegend=False)
fig.show()

In [25]:
fig2 = ndf_alignment.visualize_energy_landscape(pcd1, pcd2, T1, transform = rot, random_query = True, seed=2)
fig2.show()


In [32]:
image_folder = ndf_alignment.video_viz_path
video_name = 'se3_optimization.mp4'

ndf_alignment.render_video(
    video_name=video_name,
    image_folder=image_folder
)

IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (1100, 500) to (1104, 512) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).
